<h2 align="center">Gold Layer</h2>

The data from the silver layer is brought into the gold layer. The data in the silver layer is converted from a normalized form to a more denormalized form and stored as tables in the gold layer. The enriched tables will cater towards reporting, analytical, and visualization purposes.

**Input data:** Refined tables: ref_orders, ref_products, ref_customers

**Transformations:** 
1. An enriched table, mart_orders, is created combining data from ref_orders, ref_products, and ref_customers tables. 
2. An aggregate table, agg_profit, is created that shows the sum of profit by years, customer, product category, and product sub-category.

**Output data:** Two enriched and aggregated tables: mart_orders and agg_profit


In [0]:
%run /Users/vishnuas1987@gmail.com/PEI_Case_Study/Functions/PEI_transformation_functions

In [0]:
from pyspark.sql.functions import col,round,sum
from pyspark.sql.window import Window as w

In [0]:
try:
    #create orders,products and customers dataframe from refined tables
    df_orders = spark.table("ref_orders")
    df_products = spark.table("ref_products")
    df_customers = spark.table("ref_customers")

    #join order dataframe with customer dataframe on Customer_ID
    joined_df = df_orders.join(df_customers, "Customer_ID", "left")

    #join the new dataframe with products dataframe on Product_ID and rounded_price
    joined_df = joined_df.join(df_products, (joined_df["Product_ID"] == df_products["Product_ID"]) & (joined_df["rounded_price"] == df_products["rounded_price"]), "left")

    #create the enriched dataframe with selected fields.
    enriched_df = joined_df.select(
        col("Order_ID"),
        col("Customer_ID"),
        col("Order_year"),
        col("Customer_Name"),
        col("Country").alias("Customer_Country"),
        col("Category").alias("Product_Category"),
        col("Sub_Category").alias("Product_Sub_Category"),
        round(col("Profit"), 2).alias("Profit")
    )

    #create aggregate dataframe from the enriched dataframe 
    aggregate_df = aggregate_dataframe(enriched_df,"Order_year","Customer_ID","Product_Category", "Product_Sub_Category", "Profit")

    #join aggregated dataframe with customer_name
    aggregate_df = aggregate_df.join(df_customers["Customer_ID","Customer_Name"], "Customer_ID", "left")

    #write aggregated and enriched dataframes into delta tables
    enriched_df.write.format("delta").saveAsTable("mart_orders")
    aggregate_df.write.format("delta").saveAsTable("agg_profit")

except Exception as e:
    print("Error occurred while creating Gold layer", str(e))

In [0]:
%sql
select * from mart_orders;

Order_ID Customer_ID Order_year Customer_Name Customer_Country Product_Category Product_Sub_Category Profit CA-2016-122581 JK-15370 2016 Jay Kimmel United States Furniture Chairs 63.69 CA-2017-117485 BD-11320 2017 Bil Donatelli United States Technology Accessories 102.19 US-2016-157490 LB-16795 2016 Laurel Beltran United States Office Supplies Binders -14.92 CA-2015-111703 KB-16315 2015 Karl Braun United States Office Supplies Paper 5.64 CA-2014-108903 DO-13435 2014 Denny Ordway United States Technology Accessories -3.0 CA-2016-117583 CB-12025 2016 Cassandra Brandow United States Office Supplies Binders 38.38 CA-2014-148488 SM-20005 2014 Sally Matthias United States Office Supplies Paper 5.23 CA-2016-136434 RD-19480 2016 Rick Duston United States Furniture Furnishings 5.19 CA-2014-160094 JM-16195 2014 Justin Mac Kendrick United States Office Supplies Storage 214.0 CA-2017-141747 SC-20230 2017 Scot Coram United States Office Supplies Storage 4.18 CA-2017-132199 BO-11350 2017 Bil Overfelt United States Office Supplies Fasteners 2.8 CA-2017-107125 BD-11320 2017 Bil Donatelli United States Office Supplies Binders 41.12 CA-2017-153822 AB-10105 2017 Adrian Barton United States Office Supplies Binders -13.94 CA-2017-150091 NP-18670 2017 Nra Paige United States Technology Accessories 4.0 CA-2016-130407 KD-16270 2016 Karen Danels United States Furniture Furnishings 10.0 US-2016-105452 BF-11005 2016 Barry Franz United States Furniture Furnishings -378.4 US-2014-117058 LE-16810 2014 Laurel Elliston United States Office Supplies Binders -30.56 CA-2017-122490 TT-21070 2017 Ted Trevino United States Office Supplies Storage 10.35 US-2016-164945 CA-12055 2016 Cthy Armstrong United States Office Supplies Binders 47.0 CA-2014-111934 GD-14590 2014 Giulietta Dortch United States Office Supplies Binders 5.0 CA-2015-105627 DK-12895 2015 Dana Kaydos United States Furniture Furnishings 82.08 CA-2014-158274 RM-19675 2014 Robert Marley United States Technology Phones 131.03 CA-2014-118976 MY-18295 2014 Muhammed Ye Dwab United States Office Supplies Art 1.5 CA-2017-115882 DB-13555 2017 Dorothy Badders United States Office Supplies Paper 23.24 US-2015-126214 JS-15880 2015 John Stevenson United States Furniture Tables 356.04 CA-2017-147291 MJ-17740 2017 Max Jones United States Office Supplies Binders 421.08 US-2015-138121 JL-15835 2015 John Lee United States Furniture Chairs 38.44 CA-2015-140025 PF-19120 2015 Peter Fuller United States Office Supplies Appliances -1181.28 CA-2014-103331 KB-16315 2014 Karl Braun United States Office Supplies Paper 1.55 CA-2017-118003 DO-13645 2017 Doug O Connell United States Furniture Chairs 18.18 US-2015-129553 PG-18820 2015 Patrick Gardner United States Technology Phones 0.3 US-2017-133361 AJ-10780 2017 Anthony Jacobs United States Office Supplies Art 6.62 CA-2015-123092 JG-15115 2015 Jack Garza United States Office Supplies Binders -73.58 CA-2017-126354 SC-20380 2017 Shahi Collister United States Office Supplies Paper 40.35 CA-2015-109575 KH-16630 2015 Ken Heidel United States Technology Phones 130.0 CA-2014-111451 KL-16555 2014 Kelly Lampkin United States Office Supplies Binders -62.88 CA-2017-133256 TH-21550 2017 Tracy Hopkins United States Technology Phones 135.98 CA-2014-128888 PB-19105 2014 Peter Bhler United States Office Supplies Envelopes 204.07 CA-2016-106243 GM-14680 2016 Greg Matthias United States Furniture Bookcases -26.2 CA-2017-121503 FH-14275 2017 Frank Hawley United States Office Supplies Paper 92.44 CA-2017-156622 JP-15460 2017 Jennifer Patt United States Office Supplies Binders -9.16 CA-2014-148950 JD-16015 2014 Joy Daniels United States Office Supplies Binders -8.68 CA-2014-115812 BH-11710 2014 Brosina Hoffman United States Furniture Tables 85.31 US-2014-127978 JS-15595 2014 Ji Stevenson United States Furniture Bookcases -199.0 CA-2016-103919 TP-21565 2016 Tracy Poddar United States Furniture Furnishings -29.51 CA-2016-114972 PF-19225 2016 Phillip Flathmann United States Technology Accessories 29.03 

In [0]:
%sql
select * from agg_profit;

Customer_ID Order_year Product_Category Product_Sub_Category Total_Profit Customer_Name FG-14260 2017 Office Supplies Binders 32.67 Frank Gastineau PB-18805 2016 Office Supplies Paper 82.81 Patrick Bzostek GK-14620 2016 Technology Phones 257.59 Grace Kelly TS-21505 2016 Office Supplies Storage -4.84 Na N DM-12955 2014 Office Supplies Storage -1.26 Dario Medina EN-13780 2017 Office Supplies Art 6.55 Edward Nazzal AS-10090 2017 Office Supplies Binders -2.76 Adam Shillingsburg JG-15805 2017 Office Supplies Art 5.21 John Grady CS-12250 2015 Office Supplies Binders 49.16 Chris Selesnick PJ-18835 2015 Office Supplies Appliances 322.18 Patrick Jones MG-17890 2017 Office Supplies Storage 17.52 Michael Granlund DG-13300 2017 Technology Phones 494.97 Deirdre Greer BH-11710 2014 Furniture Furnishings 14.17 Brosina Hoffman MB-18085 2017 Office Supplies Labels 39.69 Mick Brown BK-11260 2017 Office Supplies Supplies 6.15 Berenike Kampe LC-16870 2017 Office Supplies Supplies 6.0 Na N OT-18730 2015 Office Supplies Envelopes 81.0 Olvera Toch CJ-12010 2016 Furniture Chairs 59.04 Caroline Jumper FH-14365 2015 Furniture Chairs 209.27 Fred Hopkins NP-18700 2017 Office Supplies Art 4.34 Nora Preis BG-11740 2014 Office Supplies Labels 3.22 Bruce Geld SG-20080 2015 null null 331.18 Sandra Glassco KD-16270 2015 null null 0.52 Karen Danels JD-15790 2016 null null 36.47 John Dryer RA-19285 2014 null null 0.0 Ralph Arnett CR-12580 2017 null null 20.91 Clay Rozendal SH-20395 2015 null null 2.24 Shahi Hopkins EM-14095 2017 null null 16.93 Eudokia Martin BD-11635 2015 null null 11.0 Brian Derr AB-10105 2017 Office Supplies Binders -13.94 Adrian Barton PG-18820 2015 Technology Phones 0.3 Patrick Gardner VF-21715 2014 Office Supplies Paper 8.86 Vicky Freymann DW-13540 2017 Office Supplies Appliances 33.59 Don Weiss JD-16150 2015 Furniture Furnishings -52.76 Justin Deggeller PC-18745 2016 Office Supplies Binders 24.5 Pamela Coakley AT-10735 2016 Office Supplies Binders 18.68 Annie Thurman ZC-21910 2016 Technology Accessories 64.79 Zuschuss Carroll BG-11035 2017 Office Supplies Art 3.91 Barry Gonzalez BF-11005 2017 Office Supplies Appliances 2.24 Barry Franz JF-15355 2016 Office Supplies Binders 6.53 Jay Fein SP-20860 2016 Technology Accessories 408.14 Sung Pak CS-12400 2017 Office Supplies Binders 9.14 Christopher Schild BD-11770 2016 Office Supplies Art 5.4 Bryan Davis LD-17005 2016 Technology Phones 74.81 Lisa De Cherney PB-19105 2016 Technology Phones 0.9 Peter Bhler AB-10060 2016 Office Supplies Appliances 44.89 Adam Bellavance FP-14320 2017 Technology Accessories 2.52 Frank Preis SA-20830 2017 Office Supplies Labels 10.31 Sue Ann Reed KA-16525 2017 Office Supplies Paper 6.22 Kelly Andreada MK-18160 2017 Office Supplies Storage 165.72 Mike Kennedy RB-19435 2017 Office Supplies Art 6.66 Richard Bierner LP-17095 2017 Office Supplies Art 3.15 Liz Preis JP-15460 2015 Office Supplies Envelopes 23.0 Jennifer Patt FH-14275 2016 Office Supplies Art 5.56 Frank Hawley MC-18130 2016 Office Supplies Paper 6.22 Mike Caudle TH-21235 2017 Office Supplies Supplies 2.08 Tiffany House NG-18355 2014 Office Supplies Paper 77.16000000000001 Nat Gilpin MB-17305 2015 Office Supplies Paper 3.63 Maria Bertelson DB-13660 2016 Office Supplies Storage -35.22 Duane Benoit KD-16495 2016 Furniture Furnishings 5.66 Keith Dawkins BW-11110 2017 Office Supplies Binders -10.05 Bart Watters GT-14710 2017 Technology Phones 0.7 Greg Tran SE-20110 2016 null null -290.31 Sanjit Engle JP-15460 2017 null null 7.119999999999997 Jennifer Patt JL-15850 2016 null null -13.82 John Lucas PJ-19015 2016 null null 30.4 Pauline Johnson CC-12145 2015 null null 295.81 Charles Crestani SL-20155 2014 null null 5.08 Sara Luxemburg SC-20305 2015 null null 0.0 Sean Christensen JM-16195 2017 null null 35.63 Justin Mac Kendrick RH-19510 2014 null null 10.96 Rick Huthwaite VD-21670 2014 null null 39.78 Valerie Dominguez BM-11650 2017 Technology Accessories 411.05 Brian Moss KM-16375 2017 Furniture Furnishings 16.32 Ka